In [1]:
import os
import sys
import re
import numpy as np
import pickle
from scipy.optimize import fmin
import multiprocessing as mp
import functools

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
# statmech library setup
sys.path.append('../../statmechlib')
from statmechlib.preprocessing import Trajectory, select_nodes, scale_configuration, pair_dist_cutoff
from statmechlib.forcefields import sd2_loss, utot_EAM_per_atom, utot_EAM_per_box, ftot_EAM, udif_print, u_core
from statmechlib.preprocessing import universal_eos
from statmechlib.preprocessing import pair_dist, force_targ, get_stats_EAM_per_atom, get_stats_EAM_per_box

In [4]:
target_raw = '../data/target_raw'
target_proc = '../data/target_processed'
working = '../data/working'

In [5]:
#stats_file = 'stats_marinica' # 'stats_samples'
#target_file = 'target_marinica' # 'target_samples'
stats_file = 'stats_manyknots' # 'stats_samples'
target_file = 'target_manyknots' # 'target_samples'
params_file = 'marinica_params'

In [6]:
with open(os.path.join(working, stats_file+'.pickle'), 'rb') as fi:
    stats_all = pickle.load(fi)

with open(os.path.join(working, target_file+'.pickle'), 'rb') as fi:
    targets = pickle.load(fi)

with open(os.path.join(working, params_file + '.pickle'), 'rb') as fi:
    param_list = pickle.load(fi)  

In [7]:
def find_index(select_list, full_list):
    knots = []
    for sel in select_list:
        for i, elem in enumerate(full_list):
            if abs(sel - elem) < 1e-9:
                knots.append(i)
                break
    
    assert len(knots) == len(select_list), "Knots and select_list lengths do not match"
    
    return knots

In [8]:
# find indices for chosen spline knots (this one is for Marinica potential)
pair_knots = [ 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]
edens_knots = [ 2.5,  3.1,  3.5,  4.9]


# extended knots
pair_knots = [ 2.45, 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375, 5.78]
edens_knots = [ 2.5,  3.1,  3.5,  4.9, 5.5]

pair_index = find_index(pair_knots, stats_all['hyperparams']['pair'])
edens_index = find_index(edens_knots, stats_all['hyperparams']['edens'])
print('pair_index:', pair_index)
print('edens_index:', edens_index)

('pair_index:', [2, 6, 9, 11, 17, 20, 24, 36, 45, 54, 69, 74, 80, 88, 90, 93, 101])
('edens_index:', [4, 25, 35, 75, 94])


In [9]:
# select spline knots
#pair_index = [1, 2, 3, 4, 5, 6, 9, 10, 11, 12, 13, 15, 16, 17, 18]
#edens_index = [0, 7, 8, 14]

p_ix = np.array([True if i in pair_index else False for i in range(len(stats_all['hyperparams']['pair']))])
m_ix = np.array([True if i in edens_index else False for i in range(len(stats_all['hyperparams']['edens']))])

stats = select_nodes(stats_all, p_ix, m_ix)

print("pair:", np.array(stats_all['hyperparams']['pair'])[p_ix])
print("edens:", np.array(stats_all['hyperparams']['edens'])[m_ix])
print('pars', param_list[0]['hyperparams'])

('pair:', array([ 2.45     ,  2.5648975,  2.629795 ,  2.6946925,  2.8663175,
        2.973045 ,  3.0797725,  3.5164725,  3.846445 ,  4.1764175,
        4.700845 ,  4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,
        5.4604375,  5.78     ]))
('edens:', array([ 2.5,  3.1,  3.5,  4.9,  5.5]))
('pars', {u'pair': [2.5648974999999998, 2.6297950000000001, 2.6946924999999999, 2.8663175000000001, 2.9730449999999999, 3.0797724999999998, 3.5164724999999999, 3.8464450000000001, 4.1764175000000003, 4.7008450000000002, 4.8952999999999998, 5.0897550000000003, 5.3429525, 5.4016950000000001, 5.4604375000000003], u'edens': [2.5, 3.1, 3.5, 4.9]})


In [10]:
('pair:', np.array([ 2.5648975,  2.629795 ,  2.6946925,  2.8663175,  2.973045 ,
        3.0797725,  3.5164725,  3.846445 ,  4.1764175,  4.700845 ,
        4.8953   ,  5.089755 ,  5.3429525,  5.401695 ,  5.4604375]))
('edens:', np.array([ 2.5,  3.1,  3.5,  4.9]))

('edens:', array([ 2.5,  3.1,  3.5,  4.9]))

In [11]:
multi_pars = []
for params in param_list:
    eam_params = list(params['params']['embed']) + [0.0] = list(params['params']['pair']) + [0.0] + list(params['params']['edens']) + [0.0]
    multi_pars.append(np.array(eam_params))

In [12]:
multi_pars.append(np.array([ -6.67892458e+00,  -6.69057233e-02, 0.0, -7.88558288e+02,
         8.64431119e+02,  -3.22117669e+02,   1.66223488e+01,
         1.61253439e+01,  -7.08057431e+00,   3.36500438e-01,
         1.23818786e+00,  -9.77125576e-01,  -7.10990440e-01,
         1.96923157e+00,  -7.11735164e-01,   3.61922715e-02,
        -1.61997750e+00,   1.35041921e+00,  0.0, -3.71430662e+01,
         8.77780820e-01,  -5.71131123e-02,   3.98140807e-02, 0.0]))
#multi_pars = []
multi_pars.append(np.array([ -9.42391613e+00,  -4.24391684e-02, 0.0, -2.94587357e+02,
         2.70972700e+02,  -1.04787033e+02,  -2.98238182e+00,
        -4.35229417e-01,   2.92307252e+01,  -3.93677905e+00,
         3.09415379e+00,  -2.40064822e+00,  -8.22415578e-01,
         1.49304711e+00,  -3.38081838e-02,   3.54435455e-01,
        -1.76673992e+00,   1.15161862e+00,  0.0, -3.15350855e+01,
         4.07693197e+00,  -7.52508632e-01,   3.10740894e-02, 0.0]))

multi_pars.append(np.array([ -8.15036857e+00,  -1.34492508e-01,  0.0, -6.40562492e+02,
         5.60045606e+02,  -1.62774419e+02,  -2.42163837e+01,
         4.61349632e+01,  -1.21579989e+01,   6.09852042e-01,
         1.39564841e+00,  -1.26608655e+00,  -7.44806685e-01,
         2.00404873e+00,  -6.91376693e-01,   2.17652121e-02,
        -1.61632910e+00,   1.37087609e+00,  0.0, -3.76175083e+01,
         1.56626002e+00,  -1.74622706e-01,   3.14905374e-02, 0.0]))

In [14]:
targets['relax']['energy'], len(stats['relax']['energy']), len(targets['relax']['temp'])#, stats['relax']['energy'][-2:]

([-1139.2,
  -1127.1304857789846,
  -1136.3561067610158,
  -906.9778908696875,
  -1190.2141809371096,
  -1136.7059111110157,
  -2.9688679595213743e-239],
 8,
 2)

In [15]:
targets['relax']['temp'] = [100.0, 100.0, 100.0, 100.0, 100.0, 100.0, 100.0]
stats['relax']['energy'] = stats['relax']['energy'][:-1]
stats['relax']['forces'] = stats['relax']['forces'][:-1]

In [16]:
targets['relax']['temp'], len(stats['relax']['energy'])#, stats['relax']['energy'][-2:]

([100.0, 100.0, 100.0, 100.0, 100.0, 100.0, 100.0], 7)

In [17]:
#multi_pars.append(np.array([-6.25140612e-01,  5.84924686e-05,  1.50463356e+01, -2.45628080e+00,
#        2.75467959e+00, -1.82521768e+00,  5.82623873e-01, -8.10349686e-02, 0.0]))

#for _ in range(n_walkers):
#    pars += np.random.standard_normal(multi_pars[0].shape)*0.01

In [18]:
weight_dict = {'md':5.0, 'relax':10.0, 'eos_bcc':1.0, 'eos_fcc':0.5}

for key in targets:
    targets[key]['weight'] = weight_dict[key]

In [19]:
def optimize_EAM_mp(pars, targets, stats, utot_func):
    
    output = fmin(sd2_loss, pars, args=(targets, stats, utot_EAM_per_atom, None, 0.05, 1), maxiter=100000, maxfun=100000, disp=0, full_output=1,ftol=1e-6)

    return tuple([output[1], output[0]])

In [ ]:
params_output = []

pool = mp.Pool()

for ieam in range(1):#5, len(stats_opts[it]['hyperparams'])):

    get_sd = functools.partial(sd2_loss, targets=targets, stats=stats, utot_func=utot_EAM_per_atom, ftot_func=None, dl=0.05, verbose=1)

    get_opt = functools.partial(optimize_EAM_mp, targets=targets, stats=stats, utot_func=utot_EAM_per_atom)

    # initial ordering
    print('Initial params:', multi_pars)
    
    distances = pool.map(get_sd, multi_pars)
    
    optimal_params = zip(distances, multi_pars)
    best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
    m_pars = [p[1] for p in best_params]

    print('Best params:', best_params)
    print('ieam:', ieam)
    #m_pars = multi_pars

    for i in range(6):
        optimal_params = pool.map(get_opt, m_pars)
        best_params = sorted(optimal_params, key=lambda param: param[0], reverse=True)
        m_pars = [p[1] for p in best_params]
        
        print("Iteration {}, best params: {}".format(i, best_params))

    print('Final Best params:', best_params)
    
    params_output.append(best_params)

pool.close()
pool.join()

('Initial params:', [array([ -9.42391613e+00,  -4.24391684e-02,   0.00000000e+00,
        -2.94587357e+02,   2.70972700e+02,  -1.04787033e+02,
        -2.98238182e+00,  -4.35229417e-01,   2.92307252e+01,
        -3.93677905e+00,   3.09415379e+00,  -2.40064822e+00,
        -8.22415578e-01,   1.49304711e+00,  -3.38081838e-02,
         3.54435455e-01,  -1.76673992e+00,   1.15161862e+00,
         0.00000000e+00,  -3.15350855e+01,   4.07693197e+00,
        -7.52508632e-01,   3.10740894e-02,   0.00000000e+00])])
cb md 0.999989342783
cb eos_bcc 0.998814011971
cb eos_fcc 0.997381707483
cb relax 0.99998690228
loss 0.00536040828828 0.00536040828828 0.0
('Best params:', [(0.0053604082882784069, array([ -9.42391613e+00,  -4.24391684e-02,   0.00000000e+00,
        -2.94587357e+02,   2.70972700e+02,  -1.04787033e+02,
        -2.98238182e+00,  -4.35229417e-01,   2.92307252e+01,
        -3.93677905e+00,   3.09415379e+00,  -2.40064822e+00,
        -8.22415578e-01,   1.49304711e+00,  -3.38081838e-02,
  

cb md 0.998866267703
cb eos_bcc 0.947999177555
cb eos_fcc 0.978458232924
cb relax 0.985057535889
loss 0.437471259877 0.437471259877 0.0
cb md 0.99746381609
cb eos_bcc 0.926694438074
cb eos_fcc 0.955626630523
cb relax 0.936157072749
loss 1.50919736848 1.50919736848 0.0
cb md 0.99901712653
cb eos_bcc 0.955908405835
cb eos_fcc 0.98058890594
cb relax 0.986725232139
loss 0.384228348699 0.384228348699 0.0
cb md 0.997449129212
cb eos_bcc 0.727518389747
cb eos_fcc 0.936607164663
cb relax 0.971233514489
loss 1.23938794114 1.23938794114 0.0
cb md 0.999786540116
cb eos_bcc 0.978383291555
cb eos_fcc 0.991017546351
cb relax 0.995470952819
loss 0.145170090446 0.145170090446 0.0
cb md 0.997484276507
cb eos_bcc 0.727289930734
cb eos_fcc 0.937911764533
cb relax 0.971766649708
loss 1.22744198 1.22744198 0.0
cb md 0.999830378136
cb eos_bcc 0.98250825228
cb eos_fcc 0.992307900318
cb relax 0.996501403737
loss 0.114496972837 0.114496972837 0.0
cb md 0.998639903959
cb eos_bcc 0.9546199908
cb eos_fcc 0.976819

cb eos_fcc 0.994940139541
cb relax 0.999603642588
loss 0.0640334311374 0.0640334311374 0.0
cb md 0.999992357521
cb eos_bcc 0.994360383156
cb eos_fcc 0.996729405932
cb relax 0.999902549065
loss 0.0165877050904 0.0165877050904 0.0
cb md 0.999933492585
cb eos_bcc 0.992700261833
cb eos_fcc 0.99511058044
cb relax 0.998854404477
loss 0.0430920501704 0.0430920501704 0.0
cb md 0.999982902694
cb eos_bcc 0.996589183886
cb eos_fcc 0.996839451698
cb relax 0.999831195716
loss 0.013534882407 0.013534882407 0.0
cb md 0.999925085691
cb eos_bcc 0.995166435044
cb eos_fcc 0.997240069914
cb relax 0.998731249137
loss 0.03856566559 0.03856566559 0.0
cb md 0.999970932885
cb eos_bcc 0.998803304293
cb eos_fcc 0.996467645353
cb relax 0.999604701864
loss 0.0141254613197 0.0141254613197 0.0
cb md 0.999930456889
cb eos_bcc 0.993962069807
cb eos_fcc 0.996363942983
cb relax 0.998785022097
loss 0.0407262142261 0.0407262142261 0.0
cb md 0.999974916148
cb eos_bcc 0.998667156806
cb eos_fcc 0.996657086041
cb relax 0.9996

cb md 0.999981146961
cb eos_bcc 0.997876669373
cb eos_fcc 0.997682564512
cb relax 0.99979063494
loss 0.0109424743699 0.0109424743699 0.0
cb md 0.999986324367
cb eos_bcc 0.998901111269
cb eos_fcc 0.997016906015
cb relax 0.99993422811
loss 0.00663496725877 0.00663496725877 0.0
cb md 0.99998182351
cb eos_bcc 0.997523652538
cb eos_fcc 0.997492597578
cb relax 0.999962145678
loss 0.00840204800035 0.00840204800035 0.0
cb md 0.999984219018
cb eos_bcc 0.997448089792
cb eos_fcc 0.997176367302
cb relax 0.999990977261
loss 0.0082692204398 0.0082692204398 0.0
cb md 0.999984660493
cb eos_bcc 0.998221090954
cb eos_fcc 0.996951130873
cb relax 0.999894682428
loss 0.00886907695665 0.00886907695665 0.0
cb md 0.999988562027
cb eos_bcc 0.998572489351
cb eos_fcc 0.997363628236
cb relax 0.999966524906
loss 0.00627711738175 0.00627711738175 0.0
cb md 0.999986046653
cb eos_bcc 0.997320362057
cb eos_fcc 0.997088736323
cb relax 0.99997952879
loss 0.00882330783113 0.00882330783113 0.0
cb md 0.999990564466
cb eos_

cb md 0.999986885619
cb eos_bcc 0.998713644656
cb eos_fcc 0.997491273371
cb relax 0.99996007535
loss 0.00601268113609 0.00601268113609 0.0
cb md 0.999989442919
cb eos_bcc 0.998855435225
cb eos_fcc 0.997273125414
cb relax 0.999980332904
loss 0.00551659536061 0.00551659536061 0.0
cb md 0.999987884004
cb eos_bcc 0.998685670842
cb eos_fcc 0.997241896262
cb relax 0.999974799538
loss 0.00601377843129 0.00601377843129 0.0
cb md 0.999989488012
cb eos_bcc 0.99877102482
cb eos_fcc 0.997388881801
cb relax 0.999983758903
loss 0.00550065218386 0.00550065218386 0.0
cb md 0.999988470921
cb eos_bcc 0.998699398846
cb eos_fcc 0.997436415044
cb relax 0.999968083003
loss 0.00592008173649 0.00592008173649 0.0
cb md 0.999989037694
cb eos_bcc 0.998830451766
cb eos_fcc 0.997297600923
cb relax 0.999983432093
loss 0.00548415199935 0.00548415199935 0.0
cb md 0.999991023005
cb eos_bcc 0.998629739472
cb eos_fcc 0.997278142627
cb relax 0.99997768114
loss 0.00600038912173 0.00600038912173 0.0
cb md 0.999988170589
cb

...

cb eos_fcc 0.998584473069
cb relax 0.999960431011
loss 0.00358876877467 0.00358876877467 0.0
cb md 0.999977265905
cb eos_bcc 0.999423253136
cb eos_fcc 0.998582392385
cb relax 0.999960508688
loss 0.00358872055015 0.00358872055015 0.0
cb md 0.999977307552
cb eos_bcc 0.999423376007
cb eos_fcc 0.998582640773
cb relax 0.999960460724
loss 0.00358876907715 0.00358876907715 0.0
cb md 0.999977223255
cb eos_bcc 0.999420714305
cb eos_fcc 0.998586597362
cb relax 0.999960572568
loss 0.00358874111899 0.00358874111899 0.0
cb md 0.999977184717
cb eos_bcc 0.999420835153
cb eos_fcc 0.998586637398
cb relax 0.999960572972
loss 0.00358883662673 0.00358883662673 0.0
cb md 0.999977321578
cb eos_bcc 0.99942217847
cb eos_fcc 0.998583396521
cb relax 0.999960538679
loss 0.00358870912913 0.00358870912913 0.0
cb md 0.999977243888
cb eos_bcc 0.999419960987
cb eos_fcc 0.998586338355
cb relax 0.999960648052
loss 0.0035887911357 0.0035887911357 0.0
cb md 0.999977292461
cb eos_bcc 0.99942253969
cb eos_fcc 0.99858358546

cb eos_bcc 0.999421879176
cb eos_fcc 0.998584459227
cb relax 0.999960542458
loss 0.00358869273144 0.00358869273144 0.0
cb md 0.999977371175
cb eos_bcc 0.99942121459
cb eos_fcc 0.998584393455
cb relax 0.999960561279
loss 0.00358869187795 0.00358869187795 0.0
cb md 0.999977328947
cb eos_bcc 0.999421761111
cb eos_fcc 0.998585150964
cb relax 0.999960490552
loss 0.00358867758918 0.00358867758918 0.0
cb md 0.999977338101
cb eos_bcc 0.999421963958
cb eos_fcc 0.998585500274
cb relax 0.999960446084
loss 0.00358872017801 0.00358872017801 0.0
cb md 0.999977407897
cb eos_bcc 0.999420550944
cb eos_fcc 0.99858418914
cb relax 0.999960618877
loss 0.00358870462457 0.00358870462457 0.0
cb md 0.99997728078
cb eos_bcc 0.999421992012
cb eos_fcc 0.998585082457
cb relax 0.999960494848
loss 0.0035886799888 0.0035886799888 0.0
cb md 0.999977323744
cb eos_bcc 0.999422553245
cb eos_fcc 0.998584380002
cb relax 0.99996045147
loss 0.00358869803395 0.00358869803395 0.0
cb md 0.999977310842
cb eos_bcc 0.999421776206


cb md 0.999977301037
cb eos_bcc 0.999422664151
cb eos_fcc 0.998583892105
cb relax 0.999960477016
loss 0.00358868043359 0.00358868043359 0.0
cb md 0.999977328116
cb eos_bcc 0.999421187422
cb eos_fcc 0.998585310119
cb relax 0.999960540846
loss 0.00358866837948 0.00358866837948 0.0
cb md 0.999977290494
cb eos_bcc 0.999422682986
cb eos_fcc 0.998583088076
cb relax 0.999960520358
loss 0.00358868575088 0.00358868575088 0.0
cb md 0.999977331935
cb eos_bcc 0.999421210709
cb eos_fcc 0.998585632396
cb relax 0.999960520523
loss 0.00358866765442 0.00358866765442 0.0
cb md 0.999977307546
cb eos_bcc 0.999421587721
cb eos_fcc 0.998584460373
cb relax 0.999960552907
loss 0.00358868223938 0.00358868223938 0.0
cb md 0.999977323783
cb eos_bcc 0.999421720613
cb eos_fcc 0.998584982222
cb relax 0.99996050612
loss 0.00358866769702 0.00358866769702 0.0
cb md 0.999977355888
cb eos_bcc 0.999421611922
cb eos_fcc 0.998584516092
cb relax 0.999960524268
loss 0.0035886674486 0.0035886674486 0.0
cb md 0.999977349327
cb

cb md 0.999977302449
cb eos_bcc 0.999421861738
cb eos_fcc 0.998584818572
cb relax 0.999960510866
loss 0.00358866753832 0.00358866753832 0.0
cb md 0.999977342563
cb eos_bcc 0.999421675808
cb eos_fcc 0.998584591998
cb relax 0.999960520944
loss 0.00358866345886 0.00358866345886 0.0
cb md 0.999977351872
cb eos_bcc 0.999421109579
cb eos_fcc 0.998585254848
cb relax 0.999960539566
loss 0.00358866742984 0.00358866742984 0.0
cb md 0.999977319954
cb eos_bcc 0.999422012779
cb eos_fcc 0.998584403064
cb relax 0.999960507998
loss 0.00358866342503 0.00358866342503 0.0
cb md 0.99997732609
cb eos_bcc 0.999421362757
cb eos_fcc 0.998585331126
cb relax 0.999960523321
loss 0.00358866738942 0.00358866738942 0.0
cb md 0.999977331971
cb eos_bcc 0.999421883549
cb eos_fcc 0.998584384356
cb relax 0.999960515857
loss 0.00358866329264 0.00358866329264 0.0
cb md 0.999977301283
cb eos_bcc 0.999422163392
cb eos_fcc 0.998584632176
cb relax 0.999960490608
loss 0.00358866742038 0.00358866742038 0.0
cb md 0.999977342826


cb md 0.9999773381
cb eos_bcc 0.99942152962
cb eos_fcc 0.998584754565
cb relax 0.999960529746
loss 0.00358866184224 0.00358866184224 0.0
cb md 0.99997732685
cb eos_bcc 0.999421894749
cb eos_fcc 0.998584428644
cb relax 0.999960515135
loss 0.00358866224245 0.00358866224245 0.0
cb md 0.999977326295
cb eos_bcc 0.999421671729
cb eos_fcc 0.998584529619
cb relax 0.999960532795
loss 0.00358865968141 0.00358865968141 0.0
cb md 0.99997731836
cb eos_bcc 0.9994216301
cb eos_fcc 0.998584494554
cb relax 0.999960542692
loss 0.00358865943172 0.00358865943172 0.0
cb md 0.999977349129
cb eos_bcc 0.999421627476
cb eos_fcc 0.998584381263
cb relax 0.999960533063
loss 0.00358866293082 0.00358866293082 0.0
cb md 0.99997734166
cb eos_bcc 0.999421667106
cb eos_fcc 0.998584468624
cb relax 0.999960528544
loss 0.00358866131931 0.00358866131931 0.0
cb md 0.999977339916
cb eos_bcc 0.999421624776
cb eos_fcc 0.998584663262
cb relax 0.999960523856
loss 0.00358866247526 0.00358866247526 0.0
cb md 0.999977337241
cb eos_

In [20]:
# store hyperparameters and output parameters in a single file

params_optimal = []
for pars in params_output:
    n_pair = len(stats['hyperparams']['pair'])
    n_edens = len(stats['hyperparams']['edens'])
    params_dict = {'embed':list(pars[0:2]),
                   'pair':list(pars[2:2+n_pair]),
                   'edens':list(pars[2+n_pair:])}

    params_optimal.append({'hyperparams':stats['hyperparams'],'params':params_dict})

try:
    with open(os.path.join(working, 'params_store'+'.pickle'), 'rb') as fi:
        params_store = pickle.load(fi)    
except IOError:
    print('no file')
    params_store = []
    
params_store.extend(params_optimal)

with open(os.path.join(working, "params_store.pickle"), 'wb') as fo:
    pickle.dump(params_store, fo, protocol=2)

no file
